In [ ]:
%load_ext autoreload
%autoreload 2

import os, sys
from sklearn.impute import KNNImputer
from ydata_profiling import ProfileReport
import pandas as pd, numpy as np
from sodapy import Socrata
from dotenv import load_dotenv
load_dotenv()

pd.set_option('display.max_columns', None)
sys.path.append(os.path.join(os.getcwd(), 'src'))
import src.config as config


def get_pluviosity() -> pd.DataFrame:
    file_path = os.path.join(config.path['raw_data'], 'precipitacion_la_guajira.csv')
    if not os.path.exists(file_path):
        try:
            client = Socrata(
                os.environ["SOCRATA_DOMAIN"],
                app_token=os.environ["SOCRATA_APP_TOKEN"],
                timeout=100
            )
            select = "FechaObservacion, Latitud, Longitud, UnidadMedida, ValorObservado"
            query = "Departamento = 'LA GUAJIRA' AND FechaObservacion >= '2020-01-01T00:00:00.000' AND FechaObservacion<= '2026-01-01T00:00:00.000' AND valorobservado>0"
            results = client.get(
                os.environ['PLUVIOCITY_DATASET'],
                where=query,
                select=select,
                limit=1)
            client.close()
            results_df = pd.DataFrame.from_records(results)
            results_df.to_csv(file_path, index=0)
        except Exception as e:
            client.close()
            raise e
    else:
        results_df = pd.read_csv(file_path)
    return results_df

def get_salinity() -> pd.DataFrame:
    try:
        salinity = pd.read_csv(os.environ['SALINITY_URL'])
        salinity.to_csv(os.path.join(config.path['raw_data'], '_Salinidad_Guajira.csv'), index=0)
        return salinity
    except Exception as e:
        raise e

def profile_dataset(dataset: pd.DataFrame, name: str='name_not_defined', save: bool=False) -> None:
    profile = ProfileReport(dataset, title=name)
    if save:
        # save the report as an HTML file
        profile.to_file(os.path.join(config.path['data_engineering'], f'{name}.html'))
    return profile

def select_salinity_cols(salinity: pd.DataFrame) -> pd.DataFrame:
    for col, typ in config.salinity_data_dictionary.items():
        if typ in [float, int]:
            salinity[col] = salinity[col].astype(str).str.replace('[^a-zA-Z0-9.,]', '', regex=True)
            if typ==float:
                salinity[col] = salinity[col].str.replace(',', '.', regex=True).str.replace('[a-zA-Z]+', '', regex=True)
            for i in range(5):
                salinity[col] = salinity[col].replace(' '*i, np.nan)
    salinity = salinity.astype(config.salinity_data_dictionary)
    for col, typ in config.salinity_data_dictionary.items():
        if typ in [str, 'category']:
            for i in range(5):
                salinity[col] = salinity[col].replace(' '*i, np.nan)
        if typ in [float, int]:
            salinity.loc[salinity[col]==0, col] = np.nan
    salinity.drop(config.salinity_exclude_cols, axis=1, inplace=True)
    salinity.drop(config.salinity_missing_cols, axis=1, inplace=True)
    return salinity

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [38]:
salinity_.dtypes.iloc[0]

CategoricalDtype(categories=['Aljibe', 'Manantial', 'Pozo'], ordered=False, categories_dtype=object)

In [2]:
pluviosity = get_pluviosity()
_ = profile_dataset(pluviosity, name='pluviosity_report', save=True)
salinity = get_salinity()
_ = profile_dataset(salinity, name='salinity_report', save=True)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 12/12 [00:00<00:00, 314.13it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 33/33 [00:00<00:00, 288.82it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
salinity_ = select_salinity_cols(salinity)
#excluding registers with more than 5 mising values
salinity_ = salinity_[salinity_.isna().sum(axis=1)<5]
# salinity.to_csv(os.path.join(config.path['curated_data'], 'salinity_curated.csv'), index=0)

C:\Users\MP375VC\AppData\Local\Temp\ipykernel_34900\3785613116.py:68: FutureWarning: The behavior of Series.replace (and DataFrame.replace) with CategoricalDtype is deprecated. In a future version, replace will only be used for cases that preserve the categories. To change the categories, use ser.cat.rename_categories instead.
  salinity[col] = salinity[col].replace(' '*i, np.nan)
C:\Users\MP375VC\AppData\Local\Temp\ipykernel_34900\3785613116.py:68: FutureWarning: The behavior of Series.replace (and DataFrame.replace) with CategoricalDtype is deprecated. In a future version, replace will only be used for cases that preserve the categories. To change the categories, use ser.cat.rename_categories instead.
  salinity[col] = salinity[col].replace(' '*i, np.nan)


In [59]:
profile_dataset(salinity_)

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 13/13 [00:00<00:00, 679.93it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [61]:
imputer = KNNImputer(n_neighbors=3)
imputer.fit_transform(salinity_)

ValueError: could not convert string to float: 'Pozo'

In [92]:
knn_set = salinity_[
    [col for col, typ in config.salinity_data_dictionary.items()
     if typ in [int, float] and col in salinity_.columns]
    ]
imputer = KNNImputer(n_neighbors=3)
knn_set = pd.DataFrame(data=imputer.fit_transform(knn_set), columns=knn_set.columns)

In [93]:
knn_set

X            Y  pH_seco  Cond_Seco  T_Seco     STD_seco  \
0     1299675.970  1827467.800     7.50     3060.0    31.2  1500.735655   
1     1299085.737  1828796.878     7.12     1585.0    31.4   777.341834   
2     1298371.675  1829001.292     7.07      995.0    32.7   487.984306   
3     1298003.653  1829238.533     7.37     1339.0    33.3   656.694458   
4     1299536.070  1826712.393     7.69     1553.0    31.9   761.647867   
...           ...          ...      ...        ...     ...          ...   
1533  1218411.000  1769174.000     7.29      877.6    30.0   432.000000   
1534  1225063.000  1817639.000     7.56     1259.0    34.1   617.600000   
1535  1180025.000  1767278.000     7.46     1798.0    32.5   881.700000   
1536  1171884.000  1757452.000     7.13     1128.0    31.1   553.200000   
1537  1177928.000  1767110.000     7.48     1409.0    33.1   690.800000   

      Sal_seco      CE     SAL  
0      1.68300  3060.0  1.6830  
1      0.87175  1585.0  0.8718  
2      0.54725   995.0  0.5473  
3      0.73645  1339.0  0.7365  
4      0.85415  1553.0  0.8541  
...        ...     ...     ...  
1533   0.48300   877.6  0.4830  
1534   0.67700  1259.0  0.6770  
1535   0.96100  1798.0  0.9610  
1536   0.61000  1128.0  0.6100  
1537   0.75600  1409.0  0.7560  

[1538 rows x 9 columns]

In [95]:
imputer.__dict__

{'missing_values': nan,
 'add_indicator': False,
 'keep_empty_features': False,
 'n_neighbors': 3,
 'weights': 'uniform',
 'metric': 'nan_euclidean',
 'copy': True,
 'feature_names_in_': array(['X', 'Y', 'pH_seco', 'Cond_Seco', 'T_Seco', 'STD_seco', 'Sal_seco',
        'CE', 'SAL'], dtype=object),
 'n_features_in_': 9,
 '_fit_X': array([[1.29967597e+06, 1.82746780e+06, 7.50000000e+00, ...,
         1.68300000e+00, 3.06000000e+03, 1.68300000e+00],
        [1.29908574e+06, 1.82879688e+06, 7.12000000e+00, ...,
         8.71750000e-01, 1.58500000e+03, 8.71800000e-01],
        [1.29837168e+06, 1.82900129e+06, 7.07000000e+00, ...,
         5.47250000e-01, 9.95000000e+02, 5.47300000e-01],
        ...,
        [1.18002500e+06, 1.76727800e+06, 7.46000000e+00, ...,
         9.61000000e-01, 1.79800000e+03, 9.61000000e-01],
        [1.17188400e+06, 1.75745200e+06, 7.13000000e+00, ...,
         6.10000000e-01, 1.12800000e+03, 6.10000000e-01],
        [1.17792800e+06, 1.76711000e+06, 7.48000000e+00,